In [31]:
!pip install torchsummary
!pip install scikit-learn
!pip install split-folders
!pip install pandas

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 90.2 MB/s eta 0:00:00 MB/s eta 0:00:0101


In [32]:
import os
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.autograd import Variable
import torchvision.datasets as dset
import torchvision.transforms as transforms
from torch.utils.data import DataLoader
import torchvision.models as models
import sys
import math
import splitfolders
import torchsummary
from resnet import ResNet18
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score

In [33]:
torch.cuda.is_available()

True

In [34]:
net = ResNet18(64, 47)
net.to('cuda')

torchsummary.summary(net, (3, 20, 4))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Conv2d-1            [-1, 64, 20, 4]           1,728
       BatchNorm2d-2            [-1, 64, 20, 4]             128
            Conv2d-3            [-1, 64, 20, 4]          36,864
       BatchNorm2d-4            [-1, 64, 20, 4]             128
            Conv2d-5            [-1, 64, 20, 4]          36,864
       BatchNorm2d-6            [-1, 64, 20, 4]             128
     IdentityBlock-7            [-1, 64, 20, 4]               0
            Conv2d-8            [-1, 64, 20, 4]          36,864
       BatchNorm2d-9            [-1, 64, 20, 4]             128
           Conv2d-10            [-1, 64, 20, 4]          36,864
      BatchNorm2d-11            [-1, 64, 20, 4]             128
    IdentityBlock-12            [-1, 64, 20, 4]               0
           Conv2d-13            [-1, 64, 20, 4]          36,864
      BatchNorm2d-14            [-1, 64

In [97]:
data_path = './userdata/user04'

user_dir_list = os.listdir(data_path)

user_label_list = []
for element in user_dir_list:
    label_data_path = data_path + '/' + element + '/' + element + '_label.csv'
    label_data = pd.read_csv(label_data_path)
    user_label_list.append(label_data)

df = pd.concat(user_label_list)
tmp_df = df
# df['ts'] = pd.to_datetime(df['ts'], unit='s')
df = df.sort_values('ts')
df = df.drop(columns=['actionSub', 'actionSubOption', 'condition', 'conditionSub1Option', 'conditionSub2Option', 'place', 'emotionPositive', 'emotionTension'])

df.head()

ts         action  actionOption  activity
0  1.598828e+09  personal_care           132         3
1  1.598828e+09  personal_care           132         3
2  1.598829e+09  personal_care           132         3
3  1.598829e+09  personal_care           132         3
4  1.598829e+09  personal_care           132         3

In [98]:
len(df)

22120

In [99]:
df['actionOption'].value_counts()

211    8517
121    1842
82     1810
712    1371
87     1031
41      947
756     922
212     859
724     748
793     662
711     601
725     444
132     420
751     344
133     283
213     256
752     250
43      205
122     163
81      134
46      120
84       49
762      48
92       40
42       40
722      14
Name: actionOption, dtype: int64

In [100]:
rp_data_path = './RPdata/user04/'
tmp_path = rp_data_path + '/1598828400/RP/'
tmp_list_dir = os.listdir(tmp_path)

In [101]:
tmp_list_dir.sort()
tmp_list_dir

['1598829240.png',
 '1598829300.png',
 '1598829360.png',
 '1598829420.png',
 '1598829480.png',
 '1598829540.png',
 '1598829600.png',
 '1598829660.png',
 '1598830200.png',
 '1598830260.png',
 '1598830320.png',
 '1598830380.png',
 '1598830440.png',
 '1598830500.png',
 '1598830560.png',
 '1598830620.png',
 '1598830680.png',
 '1598830740.png',
 '1598830800.png',
 '1598830860.png',
 '1598830920.png',
 '1598830980.png',
 '1598831040.png',
 '1598831100.png',
 '1598831160.png',
 '1598831220.png',
 '1598831280.png',
 '1598831340.png',
 '1598832000.png',
 '1598832060.png',
 '1598832120.png',
 '1598832180.png',
 '1598832240.png',
 '1598832300.png',
 '1598832360.png',
 '1598832420.png',
 '1598832480.png',
 '1598832540.png',
 '1598832600.png',
 '1598832660.png',
 '1598832720.png',
 '1598832780.png',
 '1598832840.png',
 '1598832900.png',
 '1598832960.png',
 '1598833020.png',
 '1598833080.png',
 '1598833140.png',
 '1598833200.png',
 '1598833260.png',
 '1598833320.png',
 '1598833380.png',
 '1598833440

In [102]:
tmp_list_dir[0][:-4]

'1598829240'

In [103]:
df[df['ts'] == 1598829240]

ts action  actionOption  activity
14  1.598829e+09   meal           121         4

In [104]:
df['ts'] = df['ts'].apply(lambda x : str(x)[:-2])

In [105]:
df

ts         action  actionOption  activity
0    1598828400  personal_care           132         3
1    1598828460  personal_care           132         3
2    1598828520  personal_care           132         3
3    1598828580  personal_care           132         3
4    1598828640  personal_care           132         3
..          ...            ...           ...       ...
764  1601208840    outdoor_act           751         4
765  1601208900    outdoor_act           751         3
766  1601208960    outdoor_act           751         3
767  1601209020    outdoor_act           751         3
768  1601209080    outdoor_act           751         3

[22120 rows x 4 columns]

In [96]:
rp_dir_list = os.listdir(rp_data_path)
rp_df = pd.DataFrame(columns = ['ts', 'rp_path'])
rp_df

for element in rp_dir_list:
    sub_list = os.listdir(rp_data_path + element + '/RP')
    for img in sub_list:
        new_row = {
            'ts' : img[:-4],
            'rp_path' : rp_data_path + element + '/RP/' + img
        }
        rp_df = rp_df.append(new_row, ignore_index=True)
    

rp_df

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

...

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_23410/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

ts                                       rp_path
0      1601192520  ./RPdata/user04/1601163000/RP/1601192520.png
1      1601182080  ./RPdata/user04/1601163000/RP/1601182080.png
2      1601191020  ./RPdata/user04/1601163000/RP/1601191020.png
3      1601200500  ./RPdata/user04/1601163000/RP/1601200500.png
4      1601192640  ./RPdata/user04/1601163000/RP/1601192640.png
...           ...                                           ...
19719  1599447960  ./RPdata/user04/1599430860/RP/1599447960.png
19720  1599433260  ./RPdata/user04/1599430860/RP/1599433260.png
19721  1599436680  ./RPdata/user04/1599430860/RP/1599436680.png
19722  1599449580  ./RPdata/user04/1599430860/RP/1599449580.png
19723  1599464700  ./RPdata/user04/1599430860/RP/1599464700.png

[19724 rows x 2 columns]

In [107]:
df = pd.merge(df, rp_df, on = 'ts')

In [108]:
df

ts       action  actionOption  activity  \
0      1598829240         meal           121         4   
1      1598829300         meal           121         3   
2      1598829360         meal           121         4   
3      1598829420         meal           121         3   
4      1598829480         meal           121         3   
...           ...          ...           ...       ...   
20390  1601208840  outdoor_act           751         4   
20391  1601208900  outdoor_act           751         3   
20392  1601208960  outdoor_act           751         3   
20393  1601209020  outdoor_act           751         3   
20394  1601209080  outdoor_act           751         3   

                                            rp_path  
0      ./RPdata/user04/1598828400/RP/1598829240.png  
1      ./RPdata/user04/1598828400/RP/1598829300.png  
2      ./RPdata/user04/1598828400/RP/1598829360.png  
3      ./RPdata/user04/1598828400/RP/1598829420.png  
4      ./RPdata/user04/1598828400/RP/1598829480.png  
...                                             ...  
20390  ./RPdata/user04/1601163000/RP/1601208840.png  
20391  ./RPdata/user04/1601163000/RP/1601208900.png  
20392  ./RPdata/user04/1601163000/RP/1601208960.png  
20393  ./RPdata/user04/1601163000/RP/1601209020.png  
20394  ./RPdata/user04/1601163000/RP/1601209080.png  

[20395 rows x 5 columns]